# Project 1: Machine Learning

In [151]:
%matplotlib inline
%load_ext autoreload
%autoreload 2
import json
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt

from typing import Tuple
from helper import load_csv_data
from processing import *
from implementations import *
from feature_expansion import *
from crossvalidation import *
from metrics import f1_score, mse_loss


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Import of the data
Import of the train and test data

In [2]:
y_train, x_train, id_train = load_csv_data("../data/train.csv")
y_test , x_test , id_test  = load_csv_data("../data/test.csv")
# print('train data shape: ', x_train.shape, y_train.shape)
# print('test  data shape: ', x_test.shape, y_test.shape)
with open('../col_name.json', 'r') as file:
    features = json.load(file)['col_names']

# Preprocess data
We pre process the data to get a clean dataset

In [3]:
x_train_cleaned = standardize(clean_data(x_train, features))

In [4]:
features = np.genfromtxt("../data/train.csv",
              delimiter=',',
              encoding='UTF-8-sig',
              dtype=None,
              names=True).dtype.names[2:]

We then divide the dataset depending on the Pri_Jet_number feature which can take values 0, 1, 2 or 3. Since the number values that are equal to 3 is really small, we will combine it with the values which have 2 so we will have a 3 subsets

### Feature expansion
We will now do feature engineering to increase the results we will have. We do degree root transformation, polynomial transformation, logarithmic transformation and reciprocical transformation.

In [95]:
x_train_finished = build_new_x(x_train_cleaned)

eoeoeoeoeoeoeoeoe!!!!!!!!!!!!!!!!!!!!!
0
0
0
0


In [5]:
X_0, y_0, X_1, y_1, X_23, y_23 = pre_process_data(x_train, y_train, features)

99913
18


In [139]:
for i in X_0:
    if(all([b.is_integer() for b in i] or all([b.is_float() for b in i]) == False):
        print(i)

SyntaxError: invalid syntax (3289958149.py, line 2)

# Cross-Validation Pipeline

cross validation pipeline. we will use 5-fold cross validation for choosing the optimal parameters.
below is the list of models we will use throughout this process.

1. least_squares (no parameter tuning needed.)
2. ridge LS 
3. mse_gd
4. mse_sgd
5. logistic
6. reg_logistic

we will optimise the weigth based on the mse loss. But the selection process will be based on observing F1 score on validation set.

To see the effect of data manipulation, we will try 3 sets of data.
1. cleaned data
2. standardized data
3. feature-engineered data

From this process, we would expect the 3rd trial would give us the best result.

In [ ]:
def func(d):
      
    for key in d:
        print("key:", key, "Value:", d[key])
          
# Driver's code
D = {'':1, 'b':2, 'c':3}
func(D)

In [33]:
ls_dict = {'tx': x_train, 'y': y_train}
least_squares(**ls_dict)

(array([ 8.03299588e-05, -7.20237523e-03, -6.05398451e-03, -5.47555763e-04,
        -1.93895382e-02,  4.73455547e-04, -2.60381502e-02,  3.25107737e-01,
        -3.80965362e-05, -2.72728860e+00, -2.21218488e-01,  9.50801264e-02,
         6.40374762e-02,  2.73554833e+00, -3.31802422e-04, -9.54328018e-04,
         2.74030502e+00, -5.34164915e-04,  9.73498603e-04,  3.69225052e-03,
         3.54487433e-04, -5.43344599e-04, -3.30448035e-01, -1.40800498e-03,
         8.31432880e-04,  1.02117272e-03, -1.68047416e-03, -5.83664815e-03,
        -1.11087998e-02,  2.72774855e+00]),
 0.33968680955669167)

In [94]:
from itertools import product

class HyperParameterTuner:
    def __init__(
        self, 
        x: np.ndarray, 
        y: np.ndarray, 
        model_name: str,
        num_folds: int,
        num_seed: int=0,
        max_iter: int=1000  
    ):

        available_models = {
        'least_squares': least_squares,
        'ridge': ridge_regression,
        'mse_gd': mean_squared_error_gd,
        'mse_sgd': mean_squared_error_sgd,
        'logistic': logistic_regression,
        'reg_logistic': reg_logistic_regression
        }

        self.x = x
        self.y = y
        self.model = available_models[model_name]
        self.model_name = model_name
        self.num_folds = num_folds
        self.num_seed  = num_seed
        self.max_iter  = max_iter
        
        # build k_indices
        np.random.seed(self.num_seed)
        self.build_k_indices()

        # get model params given model specs.
        model_parameters = {
            'least_squares': {}, 
            'ridge'        : {'lambda_': None},
            'mse_gd'       : {'initial_w': np.ones((len(y),1)), 'max_iters': self.max_iter, 'gamma': None},
            'mse_sgd'      : {'initial_w': np.ones((len(y),1)), 'max_iters': self.max_iter, 'gamma': None},
            'logistic'     : {'initial_w': np.ones((len(y),1)), 'max_iters': self.max_iter, 'gamma': None},
            'reg_logistic' : {'initial_w': np.ones((len(y),1)), 'max_iters': self.max_iter, 'gamma': None, 'lambda_': None},
        }
        self.hyp_params = model_parameters[model_name]

    def tune_(self) -> Tuple[list, float]:
        """
        hyperparameter tuning done by grid search.
        best parameters are found by finding the maximum f1 scores.
        """

        lambdas = np.logspace(-15,0,100)
        gammas  = np.linspace(0,1,100)        

        f1_scores = []
        params = self.hyp_params
        # cross validation
        if self.model_name == 'least_squares':
            results = np.array([[k, self.cross_validation_per_k(k, self.hyp_params)[-1]] for k in range(self.num_folds)])
            return results[np.argmax(results[:,-1])]   
        
        elif self.model_name == 'reg_logistic':
            lambda_and_gammas = product(gammas, lambdas)
            for (gamma, lambda_) in lambda_and_gammas:
                params['gamma'], params['lambda_'] = gamma, lambda_
                results = np.concatenate([self.cross_validation_per_k(k, params) for k in range(self.num_folds)], axis=0)
                f1_scores.append(np.mean(results, axis=0)[-1])
        
            optimum_idx = np.argmax(f1_scores)
            best_params, best_f1 = lambda_and_gammas[optimum_idx], f1_scores[optimum_idx]
            return best_params, best_f1     

        elif self.model_name == 'ridge':
            for lambda_ in lambdas:
                params['lambda_'] =lambda_
                results = np.concatenate([self.cross_validation_per_k(k, params) for k in range(self.num_folds)], axis=0)
                f1_scores.append(np.mean(results, axis=0)[-1])
                        
            optimum_idx = np.argmax(f1_scores)
            best_params, best_f1 = lambdas[optimum_idx], f1_scores[optimum_idx]
            return best_params, best_f1     
        else:
            for gamma in gammas:
                params['gamma'] = gamma
                results = np.concatenate([self.cross_validation_per_k(k, params) for k in range(self.num_folds)], axis=0)
                f1_scores.append(np.mean(results, axis=0)[-1])
            
            optimum_idx = np.argmax(f1_scores)
            best_params, best_f1 = gammas[optimum_idx], f1_scores[optimum_idx]
            return best_params, best_f1     
        

    def cross_validation_per_k(self, k: int, params: dict):
        """return the loss of given model."""
        # get k'th subgroup in test, others in train
        tr_indices, te_indices = self.k_indices[~(np.arange(self.k_indices.shape[0]) == k)].reshape(-1),\
                                 self.k_indices[k]
        
        # split the data based on train and validation indices
        y_trn, y_val = self.y[tr_indices], self.y[te_indices]
        x_trn, x_val = self.x[tr_indices], self.x[te_indices]

        # run the model
        params['tx'], params['y'] = x_trn, y_trn
        w, _ = self.model(**params)
        
        # calculate the loss for train and test data
        loss_trn = np.sqrt(mse_loss(y_trn, x_trn, w))
        loss_val = np.sqrt(mse_loss(y_val, x_val, w))
        
        # get validation f1-score
        y_pred = get_classification_pred(x_val, w)
        f1_val = f1_score(y_val, y_pred)
        return loss_trn, loss_val, f1_val

    def build_k_indices(self):
        """
        build k indices for k-fold.
        Args:
            y:      shape=(N,)
            k_fold: K in K-fold, i.e. the fold num
            seed:   the random seed

        Returns:
            A 2D array of shape=(k_fold, N/k_fold) that indicates the data indices for each fold
        """
        num_row  = self.y.shape[0]
        interval = int(num_row / self.num_folds)
        indices  = np.random.permutation(num_row)

        self.k_indices = np.array([indices[k * interval : (k + 1) * interval] for k in range(self.num_folds)])
   


In [86]:
tuner = HyperParameterTuner(x_train, y_train, 'least_squares', 5)

In [87]:
tuner.tune_()

array([2.        , 0.57177354])

# Learning algorithms

### Least squares

In [6]:
w_0, loss_0 = least_squares(y_0, X_0)
w_1, loss_1 = least_squares(y_1, X_1)
w_23, loss_23 = least_squares(y_23, X_23)
y_pred_0 = get_classification_pred(X_0, w_0)
y_pred_1 = get_classification_pred(X_1, w_1)
y_pred_23 = get_classification_pred(X_23, w_23)
print(f1_score(y_0, y_pred_0))
print(f1_score(y_1, y_pred_1))
print(f1_score(y_23, y_pred_23))

0.5592677345537758
0.530324932436679
0.6845379481959054


### Least squares with ridges regression

In [7]:
w_0, loss_0 = ridge_regression(y_0, X_0, 10)
w_1, loss_1 = ridge_regression(y_1, X_1, 10)
w_23, loss_23 = ridge_regression(y_23, X_23, 10)
y_pred_0 = get_classification_pred(X_0, w_0)
y_pred_1 = get_classification_pred(X_1, w_1)
y_pred_23 = get_classification_pred(X_23, w_23)
print(f1_score(y_0, y_pred_0))
print(f1_score(y_1, y_pred_1))
print(f1_score(y_23, y_pred_23))

0.6259504278027698
0.5559456972792309
0.6526675851584398


### Least squares with gradient descent

In [11]:
w_0, loss_0 = mean_squared_error_gd(y_0, X_0, np.ones((19,)), 100, 1e-3)
w_1, loss_1 = mean_squared_error_gd(y_1, X_1, np.ones((23,)), 100, 1e-3)
w_23, loss_23 = mean_squared_error_gd(y_23, X_23, np.ones((30,)), 100, 1e-3)
y_pred_0 = get_classification_pred(X_0, w_0)
y_pred_1 = get_classification_pred(X_1, w_1)
y_pred_23 = get_classification_pred(X_23, w_23)
print(f1_score(y_0, y_pred_0))
print(f1_score(y_1, y_pred_1))
print(f1_score(y_23, y_pred_23))

0.3424220782533286
0.4789386303865536
0.5330964394854666


### Least squares with stochastic gradient descent

In [132]:
w_0, loss_0 = mean_squared_error_sgd(y_0, X_0, np.ones((19,)), 100, 1e-3)
w_1, loss_1 = mean_squared_error_sgd(y_1, X_1, np.ones((23,)), 100, 1e-3)
w_23, loss_23 = mean_squared_error_sgd(y_23, X_23, np.ones((30,)), 100, 1e-3)
y_pred_0 = get_classification_pred(X_0, w_0)
y_pred_1 = get_classification_pred(X_1, w_1)
y_pred_23 = get_classification_pred(X_23, w_23)
print(f1_score(y_0, y_pred_0))
print(f1_score(y_1, y_pred_1))
print(f1_score(y_23, y_pred_23))

1


ValueError: operands could not be broadcast together with shapes (99913,) (99913,19) 

### Logistic regression

In [ ]:
w, l = logistic_regression(y_train, x_train_cleaned, np.ones((31,)), 1000, 1e-3)
w_0, loss_0 = mean_squared_error_sgd(y_0, X_0, np.ones((19,)), 100, 1e-3)
w_1, loss_1 = mean_squared_error_sgd(y_1, X_1, np.ones((23,)), 100, 1e-3)
w_23, loss_23 = mean_squared_error_sgd(y_23, X_23, np.ones((30,)), 100, 1e-3)
y_pred_0 = get_classification_pred(X_0, w_0)
y_pred_1 = get_classification_pred(X_1, w_1)
y_pred_23 = get_classification_pred(X_23, w_23)
print(f1_score(y_0, y_pred_0))
print(f1_score(y_1, y_pred_1))
print(f1_score(y_23, y_pred_23))

### Regularized logistic regression

In [ ]:
w, l = reg_logistic_regression(y_train, x_train_cleaned, 0.2,  np.ones((31,)), 1000, 1e-3)

# Cross validation 

In [242]:
X_0, y_0, X_1, y_1, X_23, y_23 = pre_process_data(x_train, y_train, features)

99913
18


In [115]:
X_cleaned = pre_process_whole_data(x_train, features)

In [120]:
tuner = HyperParameterTuner(X_cleaned, y_train, 'ridge', 5)

indices
[109672 143738 180135 ... 150781 235163 210763]


In [121]:
tuner.tune_()

[[ 5.64848033e-09  1.38307351e-10 -5.62474209e-09  6.82295830e-10
  -1.54363550e-08  2.90262033e-11 -3.98455676e-09 -3.37178606e-08
   3.58623334e-10  3.43351411e-07 -1.27739012e-08 -3.86730699e-08
  -2.74572725e-09 -3.44264441e-07  5.83841277e-10  3.74234050e-12
  -3.43391093e-07 -1.03198571e-09  3.28928610e-10 -2.24624270e-09
  -7.36530758e-11 -1.19963497e-11 -7.69495571e-11 -1.11538676e-10
  -5.11344687e-12 -4.09287008e-10 -2.46574472e-10  3.91791224e-10
  -3.43294346e-07]
 [ 1.38307351e-10  9.72730404e-09 -1.30840733e-09  5.26966141e-09
  -3.66296018e-08  6.23096903e-11 -1.25698827e-08  1.02935854e-07
  -8.58131705e-10 -2.24177864e-06 -1.49874470e-07  2.26662454e-08
   7.97462865e-10  2.23827831e-06 -3.10432948e-10 -3.57544670e-10
   2.23834419e-06 -1.06918134e-10 -4.54729068e-10 -7.56652655e-09
   1.22908211e-09 -2.12156411e-10  5.58918974e-10 -4.25292852e-10
  -9.58572566e-10 -9.44593105e-10  1.68311170e-10 -7.86414510e-10
   2.24203370e-06]
 [-5.62474209e-09 -1.30840733e-09  1.4

False
0.6055555555555555
[[ 5.78953830e-09  2.34022275e-10 -5.76346219e-09  8.10490627e-10
  -1.53183419e-08  2.70082592e-11 -4.03323540e-09 -3.33968371e-08
   3.61536170e-10  1.09854397e-07 -1.64340967e-08 -3.97425018e-08
  -2.31460653e-09 -1.10926299e-07  6.28287208e-10 -9.01984999e-12
  -1.09930014e-07 -8.11901844e-10  2.31457747e-10 -2.42182907e-09
  -2.38736328e-10 -1.25455981e-11 -7.00701860e-11 -1.08342446e-10
  -7.32812587e-11 -3.74247572e-10 -4.81004792e-10  1.40707420e-10
  -1.09809323e-07]
 [ 2.34022275e-10  9.77964452e-09 -1.42363322e-09  5.35440587e-09
  -3.55685947e-08  5.75165624e-11 -1.26103863e-08  1.03909126e-07
  -8.63733094e-10 -1.29013354e-06 -1.48449348e-07  2.12539771e-08
  -2.21571568e-09  1.28661719e-06 -4.08580365e-10 -2.39091175e-10
   1.28654975e-06  2.78994066e-10 -4.68821120e-10 -7.65698341e-09
   1.47190806e-09 -2.12960424e-10  5.63009009e-10 -2.73347535e-10
  -2.78158576e-10 -9.94687322e-10  8.32607801e-10  3.08259973e-10
   1.29038943e-06]
 [-5.76346219

False
0.6627734461315067
[[ 5.69060749e-09  1.65766208e-10 -5.71230220e-09  6.78640380e-10
  -1.64263772e-08  2.77642988e-11 -4.47362402e-09 -3.32610242e-08
   3.60798359e-10 -6.26551684e-07 -1.49286902e-08 -3.84401711e-08
  -1.65669999e-09  6.25662672e-07 -1.80406378e-10 -1.37302295e-10
   6.26654985e-07  1.49281842e-10  1.30633119e-10 -2.26694899e-09
  -1.92949840e-10 -3.93319934e-12 -1.08423564e-10 -1.26792740e-11
   8.32068199e-11 -4.33870227e-10 -4.67690173e-10 -3.99856227e-11
   6.26606545e-07]
 [ 1.65766208e-10  9.77100870e-09 -1.37002178e-09  5.31621982e-09
  -3.52246465e-08  6.05208380e-11 -1.24698738e-08  1.03616181e-07
  -8.69091266e-10 -1.46323289e-06 -1.50958379e-07  2.19787671e-08
  -2.55868365e-09  1.45976171e-06 -3.82340910e-10 -1.38868292e-10
   1.45973442e-06  2.40997080e-10 -4.49334852e-10 -7.64846011e-09
   1.39707861e-09 -2.03087671e-10  5.53171982e-10 -2.14856899e-10
  -6.52089018e-10 -9.36044613e-10  1.65452604e-10 -6.52304404e-10
   1.46347281e-06]
 [-5.71230220

False
0.6442518397383483
[[ 5.74164319e-09  1.61048433e-10 -5.73220353e-09  6.50324723e-10
  -1.57262743e-08  3.10083316e-11 -3.67330181e-09 -3.45998237e-08
   2.10206022e-10 -1.26498041e-08 -1.12973756e-08 -3.83104868e-08
  -1.60360701e-09  1.17987892e-08 -1.66659212e-10  1.80426879e-10
   1.25690572e-08  1.85444721e-10  2.40033940e-10 -2.35492241e-09
  -1.13901698e-10  1.34512715e-11 -8.31490693e-11  1.24680227e-10
  -3.53575770e-10 -4.39991690e-10 -4.05875903e-10  1.15539204e-10
   1.27210251e-08]
 [ 1.61048433e-10  9.80755376e-09 -1.38599284e-09  5.27114721e-09
  -3.55046132e-08  5.67007929e-11 -1.25763307e-08  1.04120109e-07
  -1.06471815e-09 -2.42716039e-06 -1.50912240e-07  2.28986220e-08
  -1.39438278e-09  2.42362816e-06 -4.07968849e-10 -1.43229240e-10
   2.42372511e-06  2.79911176e-10 -1.82083336e-10 -7.72306995e-09
   1.33233075e-09 -1.79184221e-10  5.73897382e-10 -3.72327924e-10
  -3.69564045e-10 -9.43542222e-10  2.61455603e-10  1.52992631e-10
   2.42743472e-06]
 [-5.73220353

False
0.5831648859370487
[[ 5.69360906e-09  1.50545889e-10 -5.61220115e-09  6.91995535e-10
  -1.57989063e-08  3.11515170e-11 -3.81375273e-09 -3.55382124e-08
   3.67346743e-10 -3.80740133e-07 -1.26594975e-08 -3.83019351e-08
  -3.00011112e-09  3.79817318e-07  5.86650475e-10  1.39293123e-10
   3.80661868e-07 -6.36514673e-10  1.34926870e-10 -2.26347735e-09
  -1.20739975e-10 -1.34751094e-11 -7.13592030e-11 -2.68442099e-10
  -3.21202022e-11 -4.10971674e-10 -5.82684573e-10  3.76757753e-11
   3.80792191e-07]
 [ 1.50545889e-10  9.68014750e-09 -1.29416859e-09  5.21285994e-09
  -3.61624820e-08  5.98300479e-11 -1.23707234e-08  1.01664430e-07
  -8.68407694e-10 -1.57213690e-06 -1.48817993e-07  2.27527121e-08
  -8.97258647e-10  1.56870014e-06 -1.94075338e-10 -1.25544227e-10
   1.56868595e-06  2.14069589e-10 -7.49584143e-10 -7.50197444e-09
   1.27474110e-09 -1.95072858e-10  5.63460642e-10 -5.18519195e-10
  -7.88833200e-10 -9.91009903e-10  5.09970958e-10 -1.50962599e-10
   1.57238215e-06]
 [-5.61220115

...

False
0.6743145288370628
[[ 5.69060749e-09  1.65766208e-10 -5.71230220e-09  6.78640380e-10
  -1.64263772e-08  2.77642988e-11 -4.47362402e-09 -3.32610242e-08
   3.60798359e-10 -6.26551684e-07 -1.49286902e-08 -3.84401711e-08
  -1.65669999e-09  6.25662672e-07 -1.80406378e-10 -1.37302295e-10
   6.26654985e-07  1.49281842e-10  1.30633119e-10 -2.26694899e-09
  -1.92949840e-10 -3.93319934e-12 -1.08423564e-10 -1.26792740e-11
   8.32068199e-11 -4.33870227e-10 -4.67690173e-10 -3.99856227e-11
   6.26606545e-07]
 [ 1.65766208e-10  9.77100870e-09 -1.37002178e-09  5.31621982e-09
  -3.52246465e-08  6.05208380e-11 -1.24698738e-08  1.03616181e-07
  -8.69091266e-10 -1.46323289e-06 -1.50958379e-07  2.19787671e-08
  -2.55868365e-09  1.45976171e-06 -3.82340910e-10 -1.38868292e-10
   1.45973442e-06  2.40997080e-10 -4.49334852e-10 -7.64846011e-09
   1.39707861e-09 -2.03087671e-10  5.53171982e-10 -2.14856899e-10
  -6.52089018e-10 -9.36044613e-10  1.65452604e-10 -6.52304404e-10
   1.46347281e-06]
 [-5.71230220

False
0.6721410227957263
[[ 5.74164319e-09  1.61048433e-10 -5.73220353e-09  6.50324723e-10
  -1.57262743e-08  3.10083316e-11 -3.67330181e-09 -3.45998237e-08
   2.10206022e-10 -1.26498041e-08 -1.12973756e-08 -3.83104868e-08
  -1.60360701e-09  1.17987892e-08 -1.66659212e-10  1.80426879e-10
   1.25690572e-08  1.85444721e-10  2.40033940e-10 -2.35492241e-09
  -1.13901698e-10  1.34512715e-11 -8.31490693e-11  1.24680227e-10
  -3.53575770e-10 -4.39991690e-10 -4.05875903e-10  1.15539204e-10
   1.27210251e-08]
 [ 1.61048433e-10  9.80755376e-09 -1.38599284e-09  5.27114721e-09
  -3.55046132e-08  5.67007929e-11 -1.25763307e-08  1.04120109e-07
  -1.06471815e-09 -2.42716039e-06 -1.50912240e-07  2.28986220e-08
  -1.39438278e-09  2.42362816e-06 -4.07968849e-10 -1.43229240e-10
   2.42372511e-06  2.79911176e-10 -1.82083336e-10 -7.72306995e-09
   1.33233075e-09 -1.79184221e-10  5.73897382e-10 -3.72327924e-10
  -3.69564045e-10 -9.43542222e-10  2.61455603e-10  1.52992631e-10
   2.42743472e-06]
 [-5.73220353

False
0.6705242086825973
[[ 5.69360906e-09  1.50545889e-10 -5.61220115e-09  6.91995535e-10
  -1.57989063e-08  3.11515170e-11 -3.81375273e-09 -3.55382124e-08
   3.67346743e-10 -3.80740133e-07 -1.26594975e-08 -3.83019351e-08
  -3.00011112e-09  3.79817318e-07  5.86650475e-10  1.39293123e-10
   3.80661868e-07 -6.36514673e-10  1.34926870e-10 -2.26347735e-09
  -1.20739975e-10 -1.34751094e-11 -7.13592030e-11 -2.68442099e-10
  -3.21202022e-11 -4.10971674e-10 -5.82684573e-10  3.76757753e-11
   3.80792191e-07]
 [ 1.50545889e-10  9.68014750e-09 -1.29416859e-09  5.21285994e-09
  -3.61624820e-08  5.98300479e-11 -1.23707234e-08  1.01664430e-07
  -8.68407694e-10 -1.57213690e-06 -1.48817993e-07  2.27527121e-08
  -8.97258647e-10  1.56870014e-06 -1.94075338e-10 -1.25544227e-10
   1.56868595e-06  2.14069589e-10 -7.49584143e-10 -7.50197444e-09
   1.27474110e-09 -1.95072858e-10  5.63460642e-10 -5.18519195e-10
  -7.88833200e-10 -9.91009903e-10  5.09970958e-10 -1.50962599e-10
   1.57238215e-06]
 [-5.61220115

False
0.6695830055074745
we are in  1.0


IndexError: index 24 is out of bounds for axis 0 with size 15

In [152]:
X_extended = build_poly(X_cleaned, 3)
x_test_extended = build_poly(clean_data(x_test, features), 3)
w_f,_ = ridge(y_train, X_extended, 1.9306977288832457e-11)

In [141]:
y_pred = get_classification_pred(x_test_extended, w_f)

In [153]:
y_pred = predict_labels(w_f, x_test_extended)

In [154]:
print(y_pred)

[-1. -1. -1. ...  1.  1. -1.]


In [156]:
f1_score(y_test, y_pred)

0.44992109638516414